Costruzione grafo

In [1]:
import statistics
from tqdm import tqdm

In [2]:
from collections import defaultdict

graph = defaultdict(list)

with open('wiki-topcats-reduced.txt') as f:
    for row in f.readlines():
        edges = list(map(int,row.split('\t')))
        graph[edges[0]].append(edges[1])

In [3]:
graph

defaultdict(list,
            {52: [401135, 1069112, 1163551],
             62: [12162,
              167659,
              279122,
              1089199,
              1354553,
              1400636,
              1403619,
              1537692,
              1544420],
             64: [64873],
             66: [279122, 1163290],
             74: [279122],
             95: [1179478, 1185516, 1185519, 1230865],
             103: [107],
             104: [107, 1174251, 1174302],
             105: [1174967],
             107: [104,
              142167,
              657930,
              1013995,
              1061780,
              1174302,
              1179210,
              1181401],
             108: [104, 107, 1059989, 1062426, 1161925, 1169534],
             112: [107],
             113: [279122, 1185127],
             122: [1174967],
             126: [279122],
             133: [279122, 825464],
             134: [541222,
              1060414,
              1061485,
          

Number of vertex

In [3]:
n_vert = len(graph.keys())

Number of edges

In [4]:
n_edges = sum(len(graph[k]) for k in graph.keys())

Densita del grafo

In [5]:
density = n_edges/(n_vert*(n_vert-1))

Avreage node degree

In [6]:
avreage_degree = 2*n_edges/n_vert

Dati

In [7]:
print(n_vert)
print(n_edges)
print(density)
print(avreage_degree)

428957
2645247
1.4376054956774065e-05
12.333390060075951


Load the categories

In [8]:
category_dic = {}

with open('wiki-topcats-categories.txt') as f:
    for row in f.readlines():
        category = row[:-2].split(' ')
        category_dic[category[0][9:-1]] = set(map(int,category[1:]))

In [10]:
category_dic

{'Buprestoidea': {301,
  302,
  303,
  304,
  305,
  306,
  307,
  308,
  309,
  310,
  311,
  312,
  313,
  314,
  315,
  316,
  317,
  318,
  319,
  320,
  321,
  322,
  323,
  324,
  325,
  326,
  327,
  328,
  329,
  330,
  331,
  332,
  333,
  334,
  335,
  336,
  337,
  338,
  339,
  340,
  341,
  342,
  343,
  344,
  345,
  346,
  347,
  348,
  349,
  350,
  351,
  352,
  353,
  354,
  355,
  356,
  357,
  358,
  359,
  360,
  361,
  362,
  363,
  364,
  365,
  366,
  367,
  368,
  369,
  370,
  371,
  372,
  373,
  374,
  375,
  376,
  377,
  378,
  379,
  380,
  381,
  382,
  383,
  384,
  385,
  386,
  387,
  388,
  389,
  390,
  391,
  392,
  393,
  394,
  395,
  396,
  397,
  398,
  399,
  400,
  401,
  402,
  403,
  404,
  405,
  406,
  407,
  408,
  409,
  410,
  411,
  412,
  413,
  414,
  415,
  416,
  417,
  418,
  419,
  420,
  421,
  422,
  423,
  424,
  425,
  426,
  427,
  428,
  429,
  430,
  431,
  432,
  433,
  434,
  435,
  436,
  437,
  438,
  439,
  440,
  44

Function to get the minimum path between two vertecs

In [9]:
def min_path(start,goal,graph):
    
    unvisited = set(graph.keys())
    unvisited.remove(start)
    
    verteces = set([start])
    level = 0
    while True:
        newlvl = set()
        for node in verteces:
            newlvl|=(set(graph[node]) & unvisited)
        unvisited -= verteces
        level += 1
        verteces = newlvl
        if goal in verteces:
            return level
        elif not verteces:
            return -1

Function for the distance between categories

In [10]:
def cat_dist(cat1,cat2,graph,category):
    
    verteces = set(graph.keys())
    dist_list = []
    for v1 in tqdm(category[cat1] & verteces):
        for v2 in tqdm(category[cat2] & verteces):
            v = min_path(v1,v2,graph)
            if v !=-1:
                dist_list.append(v)
            v = min_path(v2,v1,graph)
            if v !=-1:
                dist_list.append(v)
    return statistics.median(dist_list)

In [12]:
def category_order(category_dic,input_category,graph):
    l = []
    for c in tqdm(category_dic.keys()):
        try:
            l.append((c,cat_dist(c,input_category,graph,category_dic)))
        except statistics.StatisticsError:
            pass
    return sorted(l,key= lambda x:x[1])

In [ ]:
ordered_cat = category_order(category_dic,'People_from_Worcester',graph)

  0%|          | 1/17364 [01:03<306:02:18, 63.45s/it]

In [ ]:
unassigned_vertex = set(graph.keys())

block_list = []
for cat in ordered_cat:
    if not unassigned_vertex:
        break
    else:
        to_insert = unassigned_vertex & category_dic[cat[0]]
        block_list.append((cat[0],to_insert))
        unassigned_vertex-=to_insert